# Train each author as classifier
1. Either apply threshold to samples in each name group so each author classifier only trained with samples pass threshold

2. Or not apply threshold to samples so each author classifier trained with all samples (include samples can't pass threshold) 

Example: k-kim name group have 1111 samples for 57 author.

With threshold of 100:

method 1 have 504 sample for training 3 author classifier.

method 2 have 1111 sample for training 3 author classifier.

In [1]:
import os
import sys
import warnings

warnings.simplefilter(action='ignore', category=FutureWarning)

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)
    
import com_func

# parameters
#----- threshold for selecting set of name group -----------#
threshold_select_name_group = 100
#----- threshold for selecting min sample in name group ----#
threshold_lower = 10
threshold_upper = 110

apply_threshold_to_sample = True

pp_textual = ["lsa", "pv_dm", "pv_dbow"]
pp_citation = "n2v"

Dataset = "pubmed"

In [2]:
def read_labeled_file(infile):
    LabeledRecords_original = []
    with open(infile, 'r', encoding = 'utf8') as f:
        for line in f:
            read_data = line.split("\t")
            # get ride of bad formated lines
            if(len(read_data)==13 or len(read_data)==12):
                paper_detail = {"paperID": read_data[0], "authorID":read_data[1]}
                LabeledRecords_original.append(paper_detail)
            else:
                print(len(read_data))
        f.close()
    return pd.DataFrame(LabeledRecords_original)

In [3]:
# remove author(positive sample) from other(negative sample)
import random
def extractNegativeSample(positiveSample, allSample):
    negativeSample = [x for x in allSample if x not in positiveSample]
    return negativeSample

In [4]:
def extract_embedding(all_embedding, all_embedding_pid, wanted_pid_list):
    extracted_emb = []
    wanted_pid_list = wanted_pid_list.values.tolist()
    total_missing_sample = 0
    # only if embedding exist
    if len(all_embedding)>0:
        # loop through wanted pid list to keep input order
        for wanted_pid in wanted_pid_list:
            # if wanted paper in all pretrained embeddings
            if wanted_pid in all_embedding_pid:
                emb_idx = all_embedding_pid.index(wanted_pid)
                extracted_emb.append(all_embedding[emb_idx])
            # if wanted paper not in all pretrained embeddings, fill missing sample with 0's
            else:
                total_missing_sample+=1
                print("Missing Sample: ", wanted_pid)
                temp = [0] * len(all_embedding[0])
                extracted_emb.append(temp)
    print("Total missing sample: ", total_missing_sample)
    extracted_emb = pd.DataFrame(extracted_emb)
    return extracted_emb

In [5]:
from sklearn import metrics
from sklearn.model_selection import StratifiedKFold
from sklearn.metrics import precision_score, recall_score,f1_score,accuracy_score
# cross validation
def k_fold_cv(data, label, clf, k=10):
    kf = StratifiedKFold(n_splits=k, shuffle=False)
    allTrueLabel = []
    allPredLabel = []
    for train_index, test_index in kf.split(data, label):
        # print("TRAIN:", train_index, " \n TEST:", test_index)
        # split train and test
        data_train, data_test = data[train_index], data[test_index]
        label_train, label_test = label[train_index], label[test_index]
        # fit data to clf
        clf.fit(data_train, label_train)
        # get predicted label
        label_pred = clf.predict(data_test)
        allTrueLabel.extend(label_test)
        allPredLabel.extend(label_pred)
        # print("True positive: {tp}, False positive: {fp}, False negative: {fn}, True negative: {tn}"
        # .format(tp=round_tp, fp=round_fp, fn=round_fn, tn=round_tn))

    accuracy = accuracy_score(allTrueLabel, allPredLabel)
    f1 = f1_score(allTrueLabel, allPredLabel,average='macro')
    
    print(metrics.classification_report(allTrueLabel, allPredLabel))
    print(metrics.confusion_matrix(allTrueLabel, allPredLabel).ravel())
    
    return accuracy, f1

In [7]:
# load the file
import sys
import io
import os
import numpy as np
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.svm import SVC
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import confusion_matrix
from sklearn.metrics import accuracy_score
from sklearn.metrics import f1_score
from statistics import mean 

# fix random seed for reproducibility
np.random.seed(1)

fileDir = "../../Data/"+Dataset+"/canopies_labeled/"
listfiles = os.listdir(fileDir)

lr_diff_emb_f1_result = []
svm_diff_emb_f1_result = []


for select_emb in pp_textual:
    # read pretrained embeddings
    print("Load textual embedding: ", select_emb)
    all_textual_embedding, all_textual_emb_pid = com_func.read_textual_embedding(emb_type=select_emb, training_size = "3m")
    print("Load citation embedding: ", pp_citation)
    all_citation_embedding, all_citation_emb_pid = com_func.read_citation_embedding(emb_type = pp_citation)
    
    threshold_change_all_lr_f1s = []
    threshold_change_all_svm_f1s = []
    threshold_change = []
    
    # -------------- different threshold (step by 10) -----------------------#
    for step_threshold in range(threshold_lower, threshold_upper, 10):
        threshold_change.append(step_threshold)
        # collect statistic to output
        allname, positive_sample_size, negative_sample_size, total_sample_size= ([] for i in range(4))
        all_LR_accuracy, all_LR_f1, all_svcLinear_accuracy, all_svcLinear_f1 = ([] for i in range(4))
        
        total_selected_group = 0

        # read all file in labeled group
        for file in listfiles:
            # group name
            temp = file.split("_")
            name = temp[1]+"_"+temp[-1]
            print("For name: ",name)
            # read needed content in labeled file
            labeled_data = read_labeled_file(fileDir+file)
            # ---------------- collect all labeled sample -------------------- #
            # ---------------- if use all samples as negative --------------- #
            all_labeled_samples = labeled_data["paperID"].tolist()
            #----------- select name group contain productive author------------------------------------#
            #----------- (contain pair of author write more than 100 papers) ---------------------------#
            authorCounter = com_func.select_productive_groups(labeled_data, threshold_select_name_group)
            # if only have one class or no class pass the threshold, not applicable
            if(len(authorCounter)==0) or (len(authorCounter)==1):
                print(name, " pass")
            else:
                total_selected_group+= 1
                # --------------for each name group---------------- #
                if apply_threshold_to_sample == True:
                    # ---------- only use sample pass threshold ------- #
                    #-------- only select authors in name group are very productive (more than threshold)---------#
                    labeled_data, author_list, _= com_func.only_select_productive_authors(labeled_data, step_threshold)
                    # ----------------- if use filtered samples as negative  --------- #
                    filtered_all_labeled_samples = labeled_data["paperID"].tolist()
                else:
                    # ----------- use all sample in name group --------- #
                    author_list = com_func.productive_authors_list(labeled_data, step_threshold)
                    print(name, " name group sample size: ",labeled_data.shape)
                # shuffle the data
                labeled_data = labeled_data.sample(frac=1).reset_index(drop=True)
                # list of different data field
                part_collection = []
                # select feature wanted to fit to clustering/classification algorithm
                # data part, textual information
                data_part_textual = extract_embedding(all_textual_embedding, all_textual_emb_pid, labeled_data["paperID"])
                print(data_part_textual.shape)
                part_collection.append(data_part_textual)
                # data part, citation information
                data_part_citation = extract_embedding(all_citation_embedding, all_citation_emb_pid, labeled_data["paperID"])
                print(data_part_citation.shape)
                part_collection.append(data_part_citation)
                # merge different part of data data together by concatenate it all together
                combinedata = com_func.merge_data_parts(part_collection)
                print(combinedata.shape)
                # ------------- index tracker -------------------- #
                group_pid = labeled_data["paperID"].to_frame()
                counter = 0
                # loop through each author have label, one vs rest
                for author in author_list:
                    total_sample_size.append(len(labeled_data))
                    author_name = name+'_'+str(counter)
                    allname.append(author_name)
                    print(author_name, " : ", author)
                    mask = labeled_data["authorID"] == author
                    temp = labeled_data[mask]
                    positive_sample_pid = temp["paperID"].tolist()
                    negative_sample_pid = extractNegativeSample(positive_sample_pid, filtered_all_labeled_samples)
                    # append to statistic collection
                    positive_sample_size.append(len(positive_sample_pid))
                    negative_sample_size.append(len(negative_sample_pid))
                    # form positive and negative (negative class come from similar name group)
                    all_authors = []
                    all_authors.append(positive_sample_pid)
                    all_authors.append(negative_sample_pid)
                    appended_data = []
                    for label, pid in enumerate(all_authors):
                        # create df save one author data 
                        authordf = pd.DataFrame({"paperID":pid})
                        authordf['label'] = label
                        appended_data.append(authordf)
                    processed_data = pd.concat(appended_data, axis=0,ignore_index=True)

                    # alignment 
                    processed_data = pd.merge(group_pid, processed_data, on="paperID")

                    # extract true label and it's corresponeding pid for matching
                    label = processed_data["label"]
                    pid = processed_data["paperID"]

                    # using converted feature vector to train classifier
                    # using logistic regression
                    clf = LogisticRegression()
                    LRaccuracy, LRmarcof1 = k_fold_cv(combinedata, label, clf, k=10)
                    print("LR Accuracy: ",LRaccuracy)
                    print("LR F1: ", LRmarcof1)
                    all_LR_accuracy.append(LRaccuracy)
                    all_LR_f1.append(LRmarcof1)
                    # using SVM with linear kernal
                    clf = SVC(kernel='linear')
                    svcaccuracy, svcmarcof1 = k_fold_cv(combinedata, label, clf, k=10)
                    print("svc Accuracy: ",svcaccuracy)
                    print("svc F1: ", svcmarcof1)
                    all_svcLinear_accuracy.append(svcaccuracy)
                    all_svcLinear_f1.append(svcmarcof1)
                    counter+=1
        # write evaluation result to excel
        output = pd.DataFrame({'Author ':allname, "positive sample size":positive_sample_size,
                               "negative sample size":negative_sample_size, "Name group sample size": total_sample_size,
                                "logistic regression accuracy":all_LR_accuracy, "logistic regression f1": all_LR_f1,
                               "svc(linear) accuracy":all_svcLinear_accuracy, "svc(linear) f1": all_svcLinear_f1})
        savePath = "../../result/"+Dataset+"/binary_global_emb_sample=3m/"
        filename = "(Global emb sample 3m) citation = "+pp_citation+"_textual="+select_emb+"_threshold="+str(step_threshold)+"_namegroupcount="+str(total_selected_group)+".csv"
        com_func.write_csv_df(savePath, filename, output)
        print("Done")
        
        threshold_change_all_lr_f1s.append(all_LR_f1)
        threshold_change_all_svm_f1s.append(all_svcLinear_f1)
        
    lr_diff_emb_f1_result.append(threshold_change_all_lr_f1s)
    svm_diff_emb_f1_result.append(threshold_change_all_lr_f1s)

Load textual embedding:  lsa
Total textual vector records: 3151504
Vector dimension:  100
Load citation embedding:  n2v
Total citation vector records: 124922
Vector dimension:  100
For name:  j_read
j_read  pass
For name:  f_esteves
f_esteves  pass
For name:  c_miller
c_miller  pass
For name:  r_jha
r_jha  pass
For name:  a_lowe
a_lowe  pass
For name:  a_vega
a_vega  pass
For name:  k_smith
k_smith  pass
For name:  j_gordon
j_gordon  pass
For name:  s_liao
s_liao  pass
For name:  j_qian
j_qian  pass
For name:  s_bernardi
s_bernardi  pass
For name:  t_hill
t_hill  pass
For name:  s_schindler
s_schindler  pass
For name:  j_williams
j_williams  pass
For name:  s_jacobson
s_jacobson  pass
For name:  e_andrade
e_andrade  pass
For name:  t_santos
t_santos  pass
For name:  k_kim
Total sample size before apply threshold:  1111
Counter({'0000-0002-6929-5359': 211, '0000-0001-9498-284X': 154, '0000-0002-5878-8895': 139, '0000-0002-1864-3392': 92, '0000-0002-7045-8004': 57, '0000-0001-7896-6751':

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

           0       0.00      0.00      0.00        14
           1       0.99      1.00      0.99      1001

   micro avg       0.99      0.99      0.99      1015
   macro avg       0.49      0.50      0.50      1015
weighted avg       0.97      0.99      0.98      1015

[   0   14    0 1001]
svc Accuracy:  0.9862068965517241
svc F1:  0.4965277777777778
k_kim_1  :  0000-0002-1864-3392
              precision    recall  f1-score   support

           0       0.80      0.71      0.75        92
           1       0.97      0.98      0.98       923

   micro avg       0.96      0.96      0.96      1015
   macro avg       0.89      0.84      0.86      1015
weighted avg       0.96      0.96      0.96      1015

[ 65  27  16 907]
LR Accuracy:  0.9576354679802955
LR F1:  0.8641447296746261
              precision    recall  f1-score   support

           0       0.77      0.77      0.77        92
           1       0.98      0.98      0.98

/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: F-score is ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)
/home/gao137/intel/intelpython3/lib/python3.6/site-packages/sklearn/metrics/classification.py:1143: UndefinedMetricWarning: Precision and F-score are ill-defined and being set to 0.0 in labels with no predicted samples.
  'precision', 'predicted', average, warn_for)


              precision    recall  f1-score   support

           0       0.00      0.00      0.00        17
           1       0.98      1.00      0.99       998

   micro avg       0.98      0.98      0.98      1015
   macro avg       0.49      0.50      0.50      1015
weighted avg       0.97      0.98      0.97      1015

[  0  17   0 998]
LR Accuracy:  0.9832512315270936
LR F1:  0.49577744659711875


...

              precision    recall  f1-score   support

           0       0.99      1.00      1.00       487
           1       1.00      0.99      0.99       209

   micro avg       0.99      0.99      0.99       696
   macro avg       0.99      0.99      0.99       696
weighted avg       0.99      0.99      0.99       696

[486   1   3 206]
LR Accuracy:  0.9942528735632183
LR F1:  0.9931431273644389
              precision    recall  f1-score   support

           0       0.98      0.99      0.98       487
           1       0.97      0.96      0.96       209

   micro avg       0.98      0.98      0.98       696
   macro avg       0.98      0.97      0.97       696
weighted avg       0.98      0.98      0.98       696

[481   6   9 200]
svc Accuracy:  0.978448275862069
svc F1:  0.9742511499426569
For name:  w_choi
w_choi  pass
For name:  d_tavares
d_tavares  pass
For name:  l_alves
l_alves  pass
For name:  s_chan
s_chan  pass
For name:  b_ferreira
b_ferreira  pass
For name:  r_neves

s_kumar  pass
For name:  s_rocha
s_rocha  pass
For name:  t_han
t_han  pass
For name:  m_sandberg
m_sandberg  pass
For name:  j_marshall
j_marshall  pass
For name:  f_bianchi
f_bianchi  pass
For name:  c_liu
c_liu  pass
For name:  d_sanders
d_sanders  pass
For name:  r_brito
r_brito  pass
For name:  w_chang
w_chang  pass
For name:  a_murray
a_murray  pass
For name:  b_cao
b_cao  pass
For name:  k_sohn
k_sohn  pass
For name:  m_bennett
m_bennett  pass
For name:  a_sharma
a_sharma  pass
For name:  z_wei
z_wei  pass
For name:  x_gu
x_gu  pass
For name:  l_yang
l_yang  pass
For name:  h_hassan
h_hassan  pass
For name:  f_chen
f_chen  pass
For name:  g_rossi
g_rossi  pass
For name:  s_patil
s_patil  pass
For name:  m_kelly
m_kelly  pass
For name:  m_cheung
m_cheung  pass
For name:  j_weaver
j_weaver  pass
For name:  c_chien
c_chien  pass
For name:  s_yun
s_yun  pass
For name:  s_jung
s_jung  pass
For name:  e_gomes
e_gomes  pass
For name:  t_yamaguchi
t_yamaguchi  pass
For name:  p_oliveira

Total missing sample:  0
(295, 100)
Missing Sample:  15925889
Missing Sample:  12573085
Missing Sample:  21900129
Missing Sample:  18419191
Missing Sample:  17381133
Missing Sample:  17571682
Missing Sample:  11246460
Total missing sample:  7
(295, 100)
2
(295, 200)
w_wang_0  :  0000-0002-1430-1360
              precision    recall  f1-score   support

           0       0.99      0.96      0.97       101
           1       0.98      0.99      0.99       194

   micro avg       0.98      0.98      0.98       295
   macro avg       0.98      0.98      0.98       295
weighted avg       0.98      0.98      0.98       295

[ 97   4   1 193]
LR Accuracy:  0.9830508474576272
LR F1:  0.9810433240370651
              precision    recall  f1-score   support

           0       0.97      0.93      0.95       101
           1       0.96      0.98      0.97       194

   micro avg       0.97      0.97      0.97       295
   macro avg       0.97      0.96      0.96       295
weighted avg       0.97

Missing Sample:  22791448
Total missing sample:  36
(536, 100)
2
(536, 200)
r_reis_0  :  0000-0002-4295-6129
              precision    recall  f1-score   support

           0       0.99      1.00      0.99       423
           1       0.99      0.96      0.98       113

   micro avg       0.99      0.99      0.99       536
   macro avg       0.99      0.98      0.99       536
weighted avg       0.99      0.99      0.99       536

[422   1   4 109]
LR Accuracy:  0.9906716417910447
LR F1:  0.9858445969143335
              precision    recall  f1-score   support

           0       0.98      0.99      0.99       423
           1       0.97      0.93      0.95       113

   micro avg       0.98      0.98      0.98       536
   macro avg       0.98      0.96      0.97       536
weighted avg       0.98      0.98      0.98       536

[420   3   8 105]
svc Accuracy:  0.9794776119402985
svc F1:  0.9686501374480914
r_reis_1  :  0000-0002-9639-7940
              precision    recall  f1-score   

Total missing sample:  0
(470, 100)
Missing Sample:  18681453
Missing Sample:  17230295
Missing Sample:  22123305
Missing Sample:  15106978
Missing Sample:  23869171
Missing Sample:  11925252
Missing Sample:  11975590
Missing Sample:  12918967
Missing Sample:  24557432
Missing Sample:  23389421
Missing Sample:  15762711
Missing Sample:  11529720
Missing Sample:  18969699
Missing Sample:  21791181
Missing Sample:  22355459
Missing Sample:  12919039
Missing Sample:  21546871
Missing Sample:  19071448
Missing Sample:  12608813
Missing Sample:  18182398
Missing Sample:  22850941
Missing Sample:  12201775
Total missing sample:  22
(470, 100)
2
(470, 200)
j_kim_0  :  0000-0003-1835-9436
              precision    recall  f1-score   support

           0       0.98      0.98      0.98       200
           1       0.99      0.99      0.99       270

   micro avg       0.99      0.99      0.99       470
   macro avg       0.99      0.98      0.98       470
weighted avg       0.99      0.99     

In [ ]:
print(pp_textual)
print(lr_diff_emb_f1_result)
print(svm_diff_emb_f1_result)
print(threshold_change)

In [ ]:
%matplotlib inline
import matplotlib.pyplot as plt
threshold_change = np.array(threshold_change)
#--------------   logistic regression --------------------------#
# process result into np array
logistic_regression_result = np.array(combined_lr_result)
fig = plt.figure()
ax = plt.axes()
for emb_type, result in zip(combined_emb, logistic_regression_result):
    plt.plot(threshold_change, result, label=emb_type)
plt.legend()
plt.title('Average f1 for different feature in logistic regression')
plt.xlabel('Threshold')
plt.ylabel('marco f1 score')

# plt.savefig('diff_embedding_sample=3m_clf=logistic regression.eps', format='eps', dpi=300)


# -------------------- svm -------------------------------------#
svm_result = np.array(combined_svm_result)
fig = plt.figure()
ax = plt.axes()
for emb_type, result in zip(combined_emb, svm_result):
    plt.plot(threshold_change, result, label=emb_type)
plt.legend()
plt.title('Average f1 for different feature in SVM')
plt.xlabel('Threshold')
plt.ylabel('marco f1 score')

# plt.savefig('diff_embedding_sample=3m_clf=SVM.eps', format='eps', dpi=300)